<a href="https://colab.research.google.com/github/Bayaniblues/DS-Unit-2-Applied-Modeling/blob/master/Copy_of_LS_DS_232_assignment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Lambda School Data Science

*Unit 2, Sprint 3, Module 2*

---


# Wrangle ML datasets

- [ ] Continue to clean and explore your data. 
- [ ] For the evaluation metric you chose, what score would you get just by guessing?
- [ ] Can you make a fast, first model that beats guessing?

**We recommend that you use your portfolio project dataset for all assignments this sprint.**

**But if you aren't ready yet, or you want more practice, then use the New York City property sales dataset for today's assignment.** Follow the instructions below, to just keep a subset for the Tribeca neighborhood, and remove outliers or dirty data. [Here's a video walkthrough](https://youtu.be/pPWFw8UtBVg?t=584) you can refer to if you get stuck or want hints!

- Data Source: [NYC OpenData: NYC Citywide Rolling Calendar Sales](https://data.cityofnewyork.us/dataset/NYC-Citywide-Rolling-Calendar-Sales/usep-8jbt)
- Glossary: [NYC Department of Finance: Rolling Sales Data](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page)

In [127]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*
    !pip install pandas-profiling==2.*

# If you're working locally:
else:
    DATA_PATH = '../data/'

In [157]:
# Read New York City property sales data
import pandas as pd
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

Your code starts here:

In [158]:
# Change column names: replace spaces with underscores
df.columns = df.columns.str.replace(' ', '_')
df

BOROUGH             NEIGHBORHOOD  ...     SALE_PRICE   SALE_DATE
0            1                  CHELSEA  ...        $   - 0  01/01/2019
1            1                  FASHION  ...        $   - 0  01/01/2019
2            1                  FASHION  ...        $   - 0  01/01/2019
3            1   GREENWICH VILLAGE-WEST  ...        $   - 0  01/01/2019
4            1  UPPER EAST SIDE (59-79)  ...        $   - 0  01/01/2019
...        ...                      ...  ...            ...         ...
23035        4               ST. ALBANS  ...    $   510,000  04/30/2019
23036        4                SUNNYSIDE  ...    $   355,000  04/30/2019
23037        4                SUNNYSIDE  ...    $   375,000  04/30/2019
23038        4                WOODHAVEN  ...  $   1,100,000  04/30/2019
23039        4                 WOODSIDE  ...    $   569,202  04/30/2019

[23040 rows x 21 columns]

In [130]:
!pip install pandas-profiling[notebook]


In [131]:
# Get Pandas Profiling Report
from pandas_profiling import ProfileReport

profile = ProfileReport(df, title="Pandas Profiling Report")
profile

In [172]:
# Keep just the subset of data for the Tribeca neighborhood
# Check how many rows you have now. (Should go down from > 20k rows to 146)
mask = df['NEIGHBORHOOD'] == 'TRIBECA'

In [173]:
df[mask]

BOROUGH NEIGHBORHOOD  ...      SALE_PRICE   SALE_DATE
220          1      TRIBECA  ...   $   2,800,000  01/03/2019
763          1      TRIBECA  ...   $   2,650,000  01/07/2019
996          1      TRIBECA  ...         $   - 0  01/08/2019
1276         1      TRIBECA  ...   $   1,005,000  01/09/2019
1542         1      TRIBECA  ...  $   12,950,000  01/10/2019
...        ...          ...  ...             ...         ...
22221        1      TRIBECA  ...   $   5,761,259  04/24/2019
22732        1      TRIBECA  ...   $   2,600,000  04/29/2019
22733        1      TRIBECA  ...     $   605,000  04/29/2019
22897        1      TRIBECA  ...     $   960,000  04/30/2019
22898        1      TRIBECA  ...     $   975,000  04/30/2019

[146 rows x 21 columns]

In [174]:
# Q. What's the date range of these property sales in Tribeca?
df['SALE_DATE'].min()

'01/01/2019'

In [175]:
df['SALE_DATE'].max()

'04/30/2019'

In [176]:
df['SALE_PRICE'] = df['SALE_PRICE'].str.replace(' ', '')
df['SALE_PRICE'] = df['SALE_PRICE'].str.replace('$', '')
df['SALE_PRICE'] = df['SALE_PRICE'].str.replace(',', '')

df['SALE_PRICE']

0             -0
1             -0
2             -0
3             -0
4             -0
          ...   
23035     510000
23036     355000
23037     375000
23038    1100000
23039     569202
Name: SALE_PRICE, Length: 23040, dtype: object

In [177]:
# The Pandas Profiling Report showed that SALE_PRICE was read as strings
# Convert it to integers
df['SALE_PRICE'] = df['SALE_PRICE'].astype(int)
df['SALE_PRICE']

0              0
1              0
2              0
3              0
4              0
          ...   
23035     510000
23036     355000
23037     375000
23038    1100000
23039     569202
Name: SALE_PRICE, Length: 23040, dtype: int64

In [178]:
# Q. What is the maximum SALE_PRICE in this dataset?
price_max = df['SALE_PRICE'].max()
price_max

850000000

In [179]:
# Look at the row with the max SALE_PRICE
price_mask = df['SALE_PRICE'] == price_max
df[price_mask]

BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
7745        1      FASHION  ...  850000000  02/08/2019

[1 rows x 21 columns]

In [180]:
# Get value counts of TOTAL_UNITS
# Q. How many property sales were for multiple units?
total_mask = df['TOTAL_UNITS'] > 1.0
len(df[total_mask]), "for multiple units"

(7825, 'for multiple units')

In [181]:
# Keep only the single units
single_mask = df['TOTAL_UNITS'] == 1.0
len(df[single_mask]), "for single units"

(10204, 'for single units')

In [182]:
# Q. Now what is the max sales price? How many square feet does it have?
df[price_mask]['GROSS_SQUARE_FEET']

7745    697029.0
Name: GROSS_SQUARE_FEET, dtype: float64

In [183]:
# Q. How often did $0 sales occur in this subset of the data?

zero_mask = df['SALE_PRICE'] == 0
len(df[zero_mask]), '0 sales'
# There's a glossary here: 
# https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page

# It says:
# A $0 sale indicates that there was a transfer of ownership without a 
# cash consideration. There can be a number of reasons for a $0 sale including 
# transfers of ownership from parents to children. 



(6909, '0 sales')

In [184]:
# Look at property sales for > 5,000 square feet
# Q. What is the highest square footage you see?

df[df['GROSS_SQUARE_FEET'] > 5000]
greater_than = lambda a, b : df[df[a] > b] 

greater_than('GROSS_SQUARE_FEET', 5000)


BOROUGH              NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
1            1                   FASHION  ...          0  01/01/2019
2            1                   FASHION  ...          0  01/01/2019
4            1   UPPER EAST SIDE (59-79)  ...          0  01/01/2019
5            1   UPPER EAST SIDE (79-96)  ...          0  01/01/2019
6            1  UPPER WEST SIDE (96-116)  ...          0  01/01/2019
...        ...                       ...  ...        ...         ...
22950        3             CROWN HEIGHTS  ...    2100000  04/30/2019
22959        3                GREENPOINT  ...     589000  04/30/2019
22963        3               MARINE PARK  ...     480000  04/30/2019
22973        3          PROSPECT HEIGHTS  ...          0  04/30/2019
22974        3          PROSPECT HEIGHTS  ...    2200000  04/30/2019

[1220 rows x 21 columns]

In [185]:
# What are the building class categories?
# How frequently does each occur?
df['BUILDING_CLASS_CATEGORY']



0          13 CONDOS - ELEVATOR APARTMENTS
1                      21 OFFICE BUILDINGS
2                      21 OFFICE BUILDINGS
3          13 CONDOS - ELEVATOR APARTMENTS
4        15 CONDOS - 2-10 UNIT RESIDENTIAL
                       ...                
23035              01 ONE FAMILY DWELLINGS
23036         09 COOPS - WALKUP APARTMENTS
23037       10 COOPS - ELEVATOR APARTMENTS
23038              02 TWO FAMILY DWELLINGS
23039        12 CONDOS - WALKUP APARTMENTS
Name: BUILDING_CLASS_CATEGORY, Length: 23040, dtype: object

In [187]:
greater_than = lambda a, b : df[df[a] > b] 

df0 = greater_than("SALE_PRICE", 0)
df0

BOROUGH             NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
44           3      OCEAN PARKWAY-NORTH  ...     550000  01/01/2019
61           4           QUEENS VILLAGE  ...     200000  01/01/2019
65           1                  CHELSEA  ...    2000000  01/02/2019
66           1             MIDTOWN EAST  ...     330000  01/02/2019
67           1  UPPER EAST SIDE (79-96)  ...     600000  01/02/2019
...        ...                      ...  ...        ...         ...
23035        4               ST. ALBANS  ...     510000  04/30/2019
23036        4                SUNNYSIDE  ...     355000  04/30/2019
23037        4                SUNNYSIDE  ...     375000  04/30/2019
23038        4                WOODHAVEN  ...    1100000  04/30/2019
23039        4                 WOODSIDE  ...     569202  04/30/2019

[16131 rows x 21 columns]

In [193]:
# Keep subset of rows:
# Sale price more than $0, 
# Building class category = Condos - Elevator Apartments

# Check how many rows you have now. (Should be 106 rows.)


# how do i filter string value?
mask_condos = df['BUILDING_CLASS_CATEGORY'].str.contains('CONDOS', regex=False)

mask_apartments = df['BUILDING_CLASS_CATEGORY'].str.contains('ELEVATOR APARTMENTS', regex=False)

dfcondo = df[mask_condos]
dfapart = dfcondo[mask_apartments]
dfapart[mask]

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:15: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



BOROUGH NEIGHBORHOOD  ... SALE_PRICE   SALE_DATE
220          1      TRIBECA  ...    2800000  01/03/2019
763          1      TRIBECA  ...    2650000  01/07/2019
996          1      TRIBECA  ...          0  01/08/2019
1276         1      TRIBECA  ...    1005000  01/09/2019
1543         1      TRIBECA  ...    1678000  01/10/2019
...        ...          ...  ...        ...         ...
22221        1      TRIBECA  ...    5761259  04/24/2019
22732        1      TRIBECA  ...    2600000  04/29/2019
22733        1      TRIBECA  ...     605000  04/29/2019
22897        1      TRIBECA  ...     960000  04/30/2019
22898        1      TRIBECA  ...     975000  04/30/2019

[121 rows x 21 columns]

In [147]:
# Make a Plotly Express scatter plot of GROSS_SQUARE_FEET vs SALE_PRICE

X = df['GROSS_SQUARE_FEET']
Y = df['SALE_PRICE']
import plotly.express as px
fig = px.scatter(x=X, y=Y)
fig.show()

In [152]:
from numpy import *

where_are_NaNs = isnan(X)
X[where_are_NaNs] = 0

X.isna().sum()  


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



0

In [153]:
# Add an OLS (Ordinary Least Squares) trendline,
# to see how the outliers influence the "line of best fit"

import plotly.express as px

df = px.data.tips()
fig = px.scatter(df, x=X, y=Y, trendline="ols")
fig.show()


In [154]:
df.head()

total_bill   tip     sex smoker  day    time  size
0       16.99  1.01  Female     No  Sun  Dinner     2
1       10.34  1.66    Male     No  Sun  Dinner     3
2       21.01  3.50    Male     No  Sun  Dinner     3
3       23.68  3.31    Male     No  Sun  Dinner     2
4       24.59  3.61  Female     No  Sun  Dinner     4

In [155]:
# Look at sales for more than $35 million

# All are at 70 Vestry Street

# All but one have the same SALE_PRICE & SALE_DATE
# Was the SALE_PRICE for each? Or in total?
# Is this dirty data?
df2 = greater_than('SALE_PRICE', 35000000)
stree_mask = df2['ADDRESS'].str.contains('70 VESTRY STREET', regex=False)
df2[stree_mask]


KeyError: ignored

In [123]:
# Make a judgment call:
# Keep rows where sale price was < $35 million

# Check how many rows you have now. (Should be down to 90 rows.)
lesser_than = lambda a, b : df[df[a] < b] 
df5 = lesser_than("SALE_PRICE", 35000000)

maskthis = df5['ADDRESS'].str.contains('70 VESTRY STREET', regex=False)

df5[maskthis]

Empty DataFrame
Columns: [BOROUGH, NEIGHBORHOOD, BUILDING_CLASS_CATEGORY, TAX_CLASS_AT_PRESENT, BLOCK, LOT, EASE-MENT, BUILDING_CLASS_AT_PRESENT, ADDRESS, APARTMENT_NUMBER, ZIP_CODE, RESIDENTIAL_UNITS, COMMERCIAL_UNITS, TOTAL_UNITS, LAND_SQUARE_FEET, GROSS_SQUARE_FEET, YEAR_BUILT, TAX_CLASS_AT_TIME_OF_SALE, BUILDING_CLASS_AT_TIME_OF_SALE, SALE_PRICE, SALE_DATE]
Index: []

In [ ]:
# Now that you've removed outliers,
# Look again at a scatter plot with OLS (Ordinary Least Squares) trendline


In [ ]:
# Select these columns, then write to a csv file named tribeca.csv. Don't include the index.
